In [1]:
import os
from os import walk

import pandas as pd
import numpy as np
import sys
import re

import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

%matplotlib inline

pd.set_option('display.max_rows', 9000)
pd.set_option('display.max_columns', 1500)
pd.set_option('max_colwidth', 400)

In [2]:
main_folder_path = 'C:\\Users\\nikol\\OneDrive\\DTU\\11_semester\\'

resultpath = main_folder_path + '1000_genomes_results\\'

gold_standard_path = main_folder_path + 'gold_standard_data\\'

# Functions for Allele conversion

In [3]:
#Function for converting an allele to four field resolution (disregarding any trailing letters - still unambiguous)

def make_four_field(allele_high_res):
    four_field_finder = re.search(r"(A|B|C|DRB1|DQB1)\*\d{2}:\d{2,3}", allele_high_res)
    
    if four_field_finder != None:
        allele_four_field = four_field_finder.group(0)
    else:
        allele_four_field = None
    
    return allele_four_field    


def make_six_field(allele_high_res):
    six_field_finder = re.search(r"(A|B|C|DRB1|DQB1)\*\d{2}:\d{2,3}:\d{2,3}", allele_high_res)
    
    if six_field_finder != None:
        allele_six_field = six_field_finder.group(0)
    else:
        allele_six_field = None
    
    return allele_six_field     

## Function for P-type conversion

In [4]:
#Make dict for P-type conversion

p_type_filepath = gold_standard_path + 'p_group_resolution.txt'

p_type_dict = dict()

#Read the important results:
with open(p_type_filepath, 'r') as infile:
    for line in infile:
        #If several alleles map to the same one, they are separated by a "/"
        if ('/' in line) and (line[0] != '#'):
            gene = line.split('*')[0]
            
            #Only register the valid alleles:
            if gene in ['A', 'B', 'C', 'DRB1', 'DQB1']:
                        
                #Find the four field, G type resolution. The G type is found at the end of the line.
                p_type_full = gene + "*" + line.split(';')[-1][:-1]
                p_type_four_field = make_four_field(p_type_full)
            
                #Read the rest of the alleles and clean up the front and end part
                synonymous_alleles = line.split('/')
                synonymous_alleles[0] = synonymous_alleles[0].split(';')[1]
                synonymous_alleles[-1] = synonymous_alleles[-1].split(';')[0]
                

                #Convert all alleles to four field resolution
                for i in range(len(synonymous_alleles)):
                    synonymous_alleles[i] = gene + "*" + synonymous_alleles[i]
                    synonymous_alleles[i] = make_four_field(synonymous_alleles[i])

                #Remove duplicates when converting to four field:
                synonymous_allels_unique_four_field = list(set(synonymous_alleles))
                
                #Add key in dict for each of the unique entries:
                for synonymous_allele in synonymous_allels_unique_four_field:
                    
                    #Check for ambiguities in the G-type conversion e.g. C*02:02:02G and C*02:10:01G have same exon sequence for exon 2 and 3
                    if synonymous_allele in p_type_dict.keys():
                        print(synonymous_allele, p_type_full)
                    
                    p_type_dict[synonymous_allele] = p_type_full
                    

#Make P type conversion function using p_type_dict
def convert_to_p_type(allele):

    #Start by converting to four field:
    allele_four_field = make_four_field(allele)
    
    #Find corresponding P-type if it exists. If not, return the four field resolution
    if allele_four_field in p_type_dict:
        allele_four_field_p_type = p_type_dict[allele_four_field]
    else:
        allele_four_field_p_type = allele_four_field
        
    return allele_four_field_p_type


## Function for G-type conversion

In [5]:
#Make dict for G-type conversion

g_type_filepath = gold_standard_path + 'g_group_resolution.txt'

g_type_dict = dict()


#Make conversion from full allele names to G groups
with open(g_type_filepath, 'r') as infile:
    for line in infile:
        #If several alleles map to the same one, they are separated by a "/"
        if line[0] != '#':
            gene = line.split('*')[0]
            
            #Only register the valid alleles:
            if gene in ['A', 'B', 'C', 'DRB1', 'DQB1']:
                        
                #find full G type for entry - differs depending on, whether there are 1 or multiple entries in the group.
                if "/" in line:
                    g_type_full = gene + "*" + line.split(';')[-1][:-1]
                else:
                    g_type_full = gene + "*" + line.split(';')[-2]

                #For full dict (parallel to four-field dict)
                #Read the rest of the alleles and clean up the front and end part
                synonymous_alleles = line.split('/')
                synonymous_alleles[0] = synonymous_alleles[0].split(';')[1]
                synonymous_alleles[-1] = synonymous_alleles[-1].split(';')[0]
                
                #Add "gene*" in front of all alleles:
                for i in range(len(synonymous_alleles)):
                    synonymous_alleles[i] = gene + "*" + synonymous_alleles[i]
                
                #Add the group itself to the list, so that tools predicting in G-type resolution can be converted in similar fashion
                synonynous_alleles = synonymous_alleles.append(g_type_full)
                
                #Remove duplicates
                synonymous_allels_unique = sorted(list(set(synonymous_alleles)), reverse=True)
                
                #Add key in dict for each of the unique entries:
                for allele in synonymous_allels_unique :                    
                    g_type_dict[allele] = g_type_full


                    
print("Ambiguities in four-field resolution:")
print("Allele", "Primary G-group", "Alternative group", sep = "\t")
#Add entries for 4-field and 6-field resolution typings, not already found in g_type_dict.
#This is done after, in order to not overwrite ambiguous G-group mappings such as C*02:02,
#which could map to C*02:02:01 or C*02:10:01G depending on the full typing.
with open(g_type_filepath, 'r') as infile:
    for line in infile:
        #If several alleles map to the same one, they are separated by a "/"
        if line[0] != '#':
            gene = line.split('*')[0]
            
            #Only register the valid alleles:
            if gene in ['A', 'B', 'C', 'DRB1', 'DQB1']:                
                
                if "/" in line:
                    g_type_full = gene + "*" + line.split(';')[-1][:-1]
                else:
                    g_type_full = gene + "*" + line.split(';')[-2]

                #Add to four field dict (Parralel to the full dict)
                synonymous_alleles_four_field = line.split('/')
                synonymous_alleles_four_field[0] = synonymous_alleles_four_field[0].split(';')[1]
                synonymous_alleles_four_field[-1] = synonymous_alleles_four_field[-1].split(';')[0]
                                
                #Convert all alleles to four field resolution for four field typing:
                for i in range(len(synonymous_alleles_four_field)):
                    synonymous_alleles_four_field[i] = gene + "*" + synonymous_alleles_four_field[i]
                    synonymous_alleles_four_field[i] = make_four_field(synonymous_alleles_four_field[i])

                #Remove duplicates when converting to four field:
                synonymous_allels_unique_four_field = sorted(list(set(synonymous_alleles_four_field)), reverse=True)
                
                #Add key in dict for each of the unique entries:
                for allele in synonymous_allels_unique_four_field:                    
                    
                    #Only add entries, which aren't already in the dict
                    if (allele in g_type_dict.keys()):
                        
                        #For four-field: Check for ambiguities in the G-type conversion e.g. C*02:02:02G and C*02:10:01G have same exon sequence for exon 2 and 3
                        #Print the ambiguity - because of sort, nothing is added. four-field-typed-allele is kept in the group
                        if (g_type_dict[allele] != g_type_full) and ("/" in line):
                            print("Four_field_res", allele, g_type_dict[allele], g_type_full, sep=', ')
                            
                    else:
                        g_type_dict[allele] = g_type_full
                
                #Add to six field dict (Parralel to the full dict)
                synonymous_alleles_six_field = line.split('/')
                synonymous_alleles_six_field[0] = synonymous_alleles_six_field[0].split(';')[1]
                synonymous_alleles_six_field[-1] = synonymous_alleles_six_field[-1].split(';')[0]
                
                  #Convert all alleles to six field resolution for six field typing:
                for i in range(len(synonymous_alleles_six_field)):
                    synonymous_alleles_six_field[i] = gene + "*" + synonymous_alleles_six_field[i]
                    synonymous_alleles_six_field[i] = make_six_field(synonymous_alleles_six_field[i])
                    
                
                synonymous_alleles_six_field = [i for i in synonymous_alleles_six_field if i != None]
                #Remove duplicates when converting to six field:
                synonymous_allels_unique_six_field = sorted(list(set(synonymous_alleles_six_field)), reverse=True)
                
                #Add key in dict for each of the unique entries:
                for allele in synonymous_allels_unique_six_field:                    
                    
                    #Only add entries, which aren't already in the dict
                    if (allele in g_type_dict.keys()):
                        
                        #For six-field: Check for ambiguities in the G-type conversion e.g. C*02:02:02G and C*02:10:01G have same exon sequence for exon 2 and 3
                        #Print the ambiguity - because of sort, nothing is added. six-field-typed-allele is kept in the group
                        if (g_type_dict[allele] != g_type_full) and ("/" in line):
                            print("Six_field_res:", allele, g_type_dict[allele], g_type_full, sep=', ')
                            
                    else:
                        g_type_dict[allele] = g_type_full

                
                
                    
#Make G type conversion function using g_type_dict
def convert_to_g_type(allele):

    if allele in g_type_dict.keys():
        allele_g_type = g_type_dict[allele]
    else:
        allele_g_type = make_four_field(allele)
        
    return allele_g_type


Ambiguities in four-field resolution:
Allele	Primary G-group	Alternative group
Four_field_res, A*02:01, A*02:01:01G, A*02:01:02G
Four_field_res, A*23:03, A*23:03:01, A*23:03:02G
Four_field_res, A*24:02, A*24:02:01G, A*24:02:115G
Four_field_res, A*24:208, A*24:208:01, A*24:208:02G
Four_field_res, A*29:02, A*29:02:01G, A*29:02:17G
Four_field_res, A*68:01, A*68:01:01G, A*68:01:02G
Four_field_res, B*15:16, B*15:16:01G, B*15:16:02G
Four_field_res, B*27:05, B*27:05:02G, B*27:05:18G
Four_field_res, B*38:02, B*38:02:01G, B*38:02:02G
Four_field_res, B*39:02, B*39:02:01G, B*39:02:02G
Four_field_res, B*39:06, B*39:06:01, B*39:06:02G
Four_field_res, B*40:01, B*40:01:01G, B*40:01:03G
Four_field_res, B*44:281, B*44:03:01G, B*44:03:02G
Four_field_res, B*44:03, B*44:03:01G, B*44:03:02G
Four_field_res, B*51:01, B*51:01:01G, B*51:01:02G
Four_field_res, B*52:01, B*52:01:01G, B*52:01:02G
Four_field_res, B*67:01, B*67:01:01, B*67:01:02G
Four_field_res, C*02:02, C*02:02:01, C*02:02:02G
Four_field_res, C*02:

# Typing Results:

## Kourami
Save both single and ambiguous results

In [6]:
kourami_result_filepath = resultpath + 'kourami\\'

kourami_log_filepath = resultpath + 'kourami_results_from_logfiles\\'

kourami_files = list()
kourami_logfiles = list()

#Initalize result dict for single guess and for multiple typing
kourami_results = dict()
kourami_results_ambiguous = dict()


for (dirpath, dirnames, filenames) in walk(kourami_result_filepath):
    kourami_files.extend(filenames)
    
for (dirpath, dirnames, filenames) in walk(kourami_log_filepath):
    kourami_logfiles.extend(filenames)
    

for filename in kourami_files:
    #Don't include the performance logs
    if filename.endswith('.txt'):
        
        #If file is not empty:
        if os.stat(kourami_result_filepath + filename).st_size != 0:
            temp_result_list = list()
            temp_result_list_ambiguous = list()
    
            with open(kourami_result_filepath + filename, 'r') as infile:

                for line in infile:
                    #Find the first match / allele prediction
                    allele_searcher = re.search(r"(A|B|C|DRB1|DQB1)\*\d{2}:\d{2,3}:?\d{0,3}G?:?\d{0,3}", line)
                    
                    #Find all allele predictions (ambiguous). ?: is required for non-capturing groups
                    allele_searcher_ambiguous = re.findall(r"(?:A|B|C|DRB1|DQB1)\*\d{2}:\d{2,3}:?\d{0,3}G?:?\d{0,3}", line)
                    
                    if allele_searcher is not None:
                        found_allele = allele_searcher.group(0)
                                                
                        #Add to list of predictions for this sample
                        temp_result_list += [found_allele]
                        temp_result_list_ambiguous += allele_searcher_ambiguous

            #Add sample prediction to dict
            kourami_results[filename[:-4]] = temp_result_list
            kourami_results_ambiguous[filename[:-4]] = temp_result_list_ambiguous
            
        #If file is empty, take results from logfiles.    
        else:
            print("Prediction failed for: ", filename, ". Grabbing result from .log-file instead" , sep = '')
            
            log_filename = (filename[:-4] + '.log')
            
            if log_filename in kourami_logfiles:
                
                temp_result_list = list()
    
                with open(kourami_log_filepath + log_filename, 'r') as infile:
            
                    for line in infile:
                        allele_searcher = re.search(r"(A|B|C|DRB1|DQB1)\*\d{2}:\d{2,3}", line)
                        
                        if allele_searcher is not None:
                            found_allele = allele_searcher.group(0)
                            
                            temp_result_list.append(found_allele)

                kourami_results[filename[:-4]] = temp_result_list
            
            else:
                print("Unable to load results from logfile. No prediction added for", filename)         
                
#kourami_results

Prediction failed for: NA19346.txt. Grabbing result from .log-file instead
Prediction failed for: NA19471.txt. Grabbing result from .log-file instead


In [7]:
kourami_results

{'HG00096': ['A*01:01:01G',
  'A*29:02:01G',
  'B*44:03:01G',
  'B*08:01:01G',
  'C*16:01:01G',
  'C*07:01:01G',
  'DQB1*02:01:01G',
  'DQB1*02:01:01G',
  'DRB1*03:01:01G',
  'DRB1*07:01:01G'],
 'HG00097': ['A*03:01:01G',
  'A*24:02:01G',
  'C*07:02:01G',
  'C*07:02:01G',
  'DQB1*03:01:01G',
  'DQB1*06:02:01G',
  'DRB1*13:03:01',
  'DRB1*15:01:01G'],
 'HG00099': ['C*07:150',
  'C*07:150',
  'DQB1*02:01:01G',
  'DQB1*03:01:01G',
  'DRB1*11:01:01G',
  'DRB1*03:01:01G'],
 'HG00100': ['A*01:01:01G',
  'A*01:01:01G',
  'B*57:11',
  'B*08:01:01G',
  'C*07:01:01G',
  'C*06:02:01G',
  'DQB1*03:03:02G',
  'DQB1*02:01:01G',
  'DRB1*03:01:01G',
  'DRB1*07:01:01G'],
 'HG00101': ['A*32:01:01G',
  'A*11:50',
  'B*57:01:01G',
  'B*27:05:02G',
  'C*02:02:02G',
  'C*06:02:01G',
  'DQB1*03:02:01G',
  'DQB1*06:02:01G',
  'DRB1*04:04:01',
  'DRB1*15:01:01G'],
 'HG00102': ['A*01:01:01G',
  'A*01:01:01G',
  'B*07:02:01G',
  'B*08:94',
  'C*07:02:01G',
  'C*07:01:01G',
  'DQB1*05:01:01G',
  'DQB1*03:01:01G',

## HLA-LA

In [8]:
hla_la_result_filepath = resultpath + 'hla-la\\'

hla_la_files = []
for (dirpath, dirnames, filenames) in walk(hla_la_result_filepath):
    hla_la_files.extend(filenames)
    
#print(hla_la_files)


hla_la_results = dict()

for filename in hla_la_files:
    if filename.endswith('.txt'):
        temp_results_0 = pd.read_csv(hla_la_result_filepath + filename, sep = "\t")['Allele']
        temp_results = [i for i in temp_results_0 if i.startswith(('A', 'B', 'C', 'DRB1', 'DQB1'))]

        hla_la_results[filename[:-4]] = temp_results


#hla_la_results

## Optitype

In [9]:
optitype_result_filepath = resultpath + 'optitype\\'

optitype_files = []
for (dirpath, dirnames, filenames) in walk(optitype_result_filepath):
    optitype_files.extend(filenames)
    
#print(optitype_files)


optitype_results = dict()

for filename in optitype_files:
    if filename.endswith('.txt'):
        temp_results = list(pd.read_csv(optitype_result_filepath + filename, sep = "\t").iloc[0])[1:7]

        temp_results_filtered = [i for i in temp_results if isinstance(i,str)]
        optitype_results[filename[:-4]] = temp_results_filtered

#optitype_results

## Hisatgenotype

In [10]:
hisatgenotype_result_filepath = resultpath + 'hisatgenotype\\'

hisatgenotype_files = []
for (dirpath, dirnames, filenames) in walk(hisatgenotype_result_filepath):
    hisatgenotype_files.extend(filenames)
    
#print(hisatgenotype_files)

#Save two predictions. One, with one guess per allele and one with the full prediction
hisatgenotype_results = dict()

for filename in hisatgenotype_files:
    if filename.endswith('.txt'):
    
        hisatgenotype_resultlist = list()
        
        hisatgenotype_resultlist_ambiguous = list()
      
        with open(hisatgenotype_result_filepath + filename) as infile:
            for line in infile:
                result = re.match(r'^\t+(1|2)\sranked (A|B|C|DRB1|DQB1)',line)
            
                if result is not None:
                    hisatgenotype_resultlist.append(line.split()[2])              
                     
            #Duplicate prediction for an allele in case of homologous case, so that each gene has two predictions.
            #In a homologous case, both result dicts only have one prediction and both needs an update.
            for allele in ['A', 'B', 'C', 'DRB1', 'DQB1']:
                allele_list = [pred for pred in hisatgenotype_resultlist if pred.startswith(allele)]

                if len(allele_list) == 1:
                    hisatgenotype_resultlist.append(allele_list[0])
                    hisatgenotype_resultlist.sort()

        hisatgenotype_results[filename[:-4]] = hisatgenotype_resultlist
                
#hisatgenotype_results           
        

## STC-seq

In [11]:
def flatten(a):
    return [item for sublist in a for item in sublist]

In [37]:
stc_seq_result_filepath = resultpath + 'stc-seq\\'

stc_seq_files = []
for (dirpath, dirnames, filenames) in walk(stc_seq_result_filepath):
    stc_seq_files.extend(filenames)
    
#print(stc_seq_files)

stc_seq_results = dict()

for filename in stc_seq_files:
    if filename.endswith('.txt'):
        filename = 'HG00096.txt'
        stc_df = pd.read_csv(stc_seq_result_filepath + filename, sep = "\t").reset_index()
        stc_df.columns = stc_df.iloc[0]
        stc_list = list(stc_df[stc_df['Locus'].isin(['A', 'B', 'C','DRB1', 'DQB1'])]['Genotype'])
        
        temp_results =  flatten([i.split(',') for i in stc_list])
        
       
        stc_seq_results[filename[:-4]] = temp_results
    
        sys.exit()
#stc_seq_results

SystemExit: 

C:\Users\nikol\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3304: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [15]:
kourami_results_ambiguous

{'HG00096': ['A*01:01:01G',
  'A*29:02:01G',
  'B*44:03:01G',
  'B*08:01:01G',
  'C*16:01:01G',
  'C*07:01:01G',
  'DQB1*02:01:01G',
  'DQB1*02:01:01G',
  'DRB1*03:01:01G',
  'DRB1*07:01:01G'],
 'HG00097': ['A*03:01:01G',
  'A*24:02:01G',
  'C*07:02:01G',
  'C*07:02:01G',
  'DQB1*03:01:01G',
  'DQB1*06:02:01G',
  'DRB1*13:03:01',
  'DRB1*15:01:01G'],
 'HG00099': ['C*07:150',
  'C*07:150',
  'DQB1*02:01:01G',
  'DQB1*03:01:01G',
  'DRB1*11:01:01G',
  'DRB1*03:01:01G'],
 'HG00100': ['A*01:01:01G',
  'A*01:01:01G',
  'B*57:11',
  'B*57:83',
  'B*08:01:01G',
  'C*07:01:01G',
  'C*06:02:01G',
  'DQB1*03:03:02G',
  'DQB1*02:01:01G',
  'DRB1*03:01:01G',
  'DRB1*07:01:01G'],
 'HG00101': ['A*32:01:01G',
  'A*11:50',
  'B*57:01:01G',
  'B*27:05:02G',
  'C*02:02:02G',
  'C*06:02:01G',
  'DQB1*03:02:01G',
  'DQB1*06:02:01G',
  'DRB1*04:04:01',
  'DRB1*15:01:01G'],
 'HG00102': ['A*01:01:01G',
  'A*01:01:01G',
  'B*07:02:01G',
  'B*08:94',
  'C*07:02:01G',
  'C*07:01:01G',
  'DQB1*05:01:01G',
  'DQB

In [16]:
stc_seq_alt_list

['A*01:11N,A*01:22N;A*01:11N,A*01:81;A*01:22N,A*01:81;A*01:22N,A*36:01;A*01:81,A*36:01',
 'B*08:134,B*44:184;B*08:134,B*44:26',
 'C*07:514,C*16:80',
 'DQB1*02:01:01,DQB1*02:02:03']

In [17]:
test = flatten([i.replace(';',',').split(',') for i in stc_seq_alt_list])

In [18]:
test

['A*01:11N',
 'A*01:22N',
 'A*01:11N',
 'A*01:81',
 'A*01:22N',
 'A*01:81',
 'A*01:22N',
 'A*36:01',
 'A*01:81',
 'A*36:01',
 'B*08:134',
 'B*44:184',
 'B*08:134',
 'B*44:26',
 'C*07:514',
 'C*16:80',
 'DQB1*02:01:01',
 'DQB1*02:02:03']

In [19]:
list(set(test[::2]))

['A*01:11N', 'DQB1*02:01:01', 'A*01:22N', 'A*01:81', 'C*07:514', 'B*08:134']

In [20]:
list(set(test[1::2]))

['C*16:80',
 'A*01:22N',
 'A*01:81',
 'B*44:184',
 'DQB1*02:02:03',
 'A*36:01',
 'B*44:26']

## Depth analysis

In [21]:
#load data
depth_filepath = resultpath + 'depth\\'

depth_files = []
for (dirpath, dirnames, filenames) in walk(depth_filepath):

    depth_files.extend(filenames)

depth_results = dict()

for filename in depth_files:
    
    if filename.endswith('.depth.mosdepth.summary.txt'):
        temp_results = pd.read_csv(depth_filepath + filename, sep='\t')
        
        temp_results.set_index('chrom', inplace=True)
        
        mean_region_depth = temp_results.loc['total_region', 'mean']
        depth_results[filename[0:7]] = mean_region_depth
    
#depth_results

# Load Gold standard data

In [22]:
MG_exome_merged_df = pd.read_pickle(gold_standard_path + "MG_exome_merged_df.pkl")

gs_four_field_df = pd.read_pickle(gold_standard_path + "gs_four_field_df.pkl")

gs_p_group_df = pd.read_pickle(gold_standard_path + "gs_p_group_df.pkl")

gs_g_group_df = pd.read_pickle(gold_standard_path + "gs_g_group_df.pkl")

In [23]:
gold_standard_id_list = list(MG_exome_merged_df.index)

# Majority Votes

In [24]:
def most_frequent(List): 
    return max(set(List), key = List.count) 

### All 5

In [25]:
def get_prediction(result_dict, subject, allele):
    try:
        result = sorted([pred for pred in result_dict[subject] if pred.startswith(allele)])
    except KeyError as error:
        result = ''
        
    return result

In [26]:
from collections import Counter

all_five_results = dict()

for subject in gold_standard_id_list:
    
    all_five_results[subject] = list()

    for allele in ['A', 'B', 'C', 'DRB1', 'DQB1']:
        #Get list of all predictions:
        kourami_pred = get_prediction(kourami_results, subject, allele)
        hisatgenotype_pred = get_prediction(hisatgenotype_results, subject, allele)
        hla_la_pred = get_prediction(hla_la_results, subject, allele)
        optitype_pred = get_prediction(optitype_results, subject, allele)
        stc_seq_pred = get_prediction(stc_seq_results, subject, allele)
        
        
        
        all_predictions_list = [kourami_pred, hisatgenotype_pred, hla_la_pred, optitype_pred, stc_seq_pred]
        
        all_predictions_list_clean = [preds for preds in all_predictions_list if (preds != []) and (preds != '')]
        
        all_predictions_list_transposed = list(map(list, zip(*all_predictions_list_clean)))
        
        preds_count_1 = Counter(all_predictions_list_transposed[0])
        preds_count_2 = Counter(all_predictions_list_transposed[1])
        
        mode_1 = preds_count_1.most_common(1)[0][0]
        mode_2 = preds_count_2.most_common(1)[0][0]
        

        all_five_results[subject].extend([mode_1, mode_2])
    

### HLA-LA, Kourami, Hisatgenotype

In [27]:
from collections import Counter

graph_tools_results = dict()

for subject in gold_standard_id_list:
    
    graph_tools_results[subject] = list()

    for allele in ['A', 'B', 'C', 'DRB1', 'DQB1']:
        #Get list of all predictions:
        kourami_pred = get_prediction(kourami_results, subject, allele)
        hisatgenotype_pred = get_prediction(hisatgenotype_results, subject, allele)
        hla_la_pred = get_prediction(hla_la_results, subject, allele)
        optitype_pred = get_prediction(optitype_results, subject, allele)
        stc_seq_pred = get_prediction(stc_seq_results, subject, allele)
        
        
        
        all_predictions_list = [kourami_pred, hla_la_pred, hisatgenotype_pred]
        
        all_predictions_list_clean = [preds for preds in all_predictions_list if (preds != []) and (preds != '')]
        
        all_predictions_list_transposed = list(map(list, zip(*all_predictions_list_clean)))
        
        preds_count_1 = Counter(all_predictions_list_transposed[0])
        preds_count_2 = Counter(all_predictions_list_transposed[1])
        
        mode_1 = preds_count_1.most_common(1)[0][0]
        mode_2 = preds_count_2.most_common(1)[0][0]
        
        graph_tools_results[subject].extend([mode_1, mode_2])
    

# Results 1000 Genome (only 2014 data)

Future work: Implement intersection over union as a performance metric

# Calculate Results

In [28]:
def check_result(correct_alleles_list, tool_result_dict, subject_key, tool_name, allele):
    try:
        hit_1 = set(correct_alleles_list[0]).intersection(tool_result_dict[subject_key])
        hit_2 = set(correct_alleles_list[1]).intersection(tool_result_dict[subject_key])
    except KeyError as error:
        hit_1 = ''
        hit_2 = ''
    
    #In the case of homozygosity
    if (correct_alleles_list[0] == correct_alleles_list[1]):
        try:
            hit_1 = [''] * tool_result_dict[subject_key].count(correct_alleles_list[0][0])
            hit_2 = ''
        except KeyError as error:
            hit_1 = ''
            hit_2 = ''            
    
    #Register mistakes, if tool didn't get both alleles correct
    if (len(hit_1)+len(hit_2) != 2):
        print(subject_key)
        print(tool_name, tool_result_dict[subject_key])
        print(correct_alleles_list)
        print("\n")
        #Only register mistakes for optitype for HLA-A, HLA-B and HLA-C
        if allele in ['A', 'B', 'C']:
            error_dataframe_hla_I.loc[subject_key, tool_name]  += 2 - (len(hit_1)+len(hit_2))
        
        elif tool_name == 'Optitype':
            pass
        
        else:
            error_dataframe_hla_II.loc[subject_key, tool_name]  += 2 - (len(hit_1)+len(hit_2))
        
#         print(subject_key)
#         print(correct_alleles_list)
#         print(tool_result_dict[subject_key])
        
        
    return len(hit_1)+len(hit_2)

#Get the number of predictions from a tool for a specific allele for a specific subject (2 or 0)
def get_count(allele, pred_dict, subject):
    try:
        output = len([pred for pred in pred_dict[subject] if pred.startswith(allele)])
    except KeyError as error:
        output = 0
        
    return output

In [32]:
idx = pd.IndexSlice

#Create dataframe over samples which the tools didn't predict right:

error_dataframe_hla_I = pd.DataFrame({'mean_depth' : depth_results})

for tool in ['Kourami', 'HLA-LA', 'Optitype', 'Hisatgenotype', 'STC-seq', 'ensemble_all', 'ensemble_graph']:
    error_dataframe_hla_I[tool] = 0

    
error_dataframe_hla_II = pd.DataFrame({'mean_depth' : depth_results})

for tool in ['Kourami', 'HLA-LA', 'Hisatgenotype', 'STC-seq', 'ensemble_all', 'ensemble_graph']:
    error_dataframe_hla_II[tool] = 0    

    
#Create score dataframe:
tool_extended_list = ['Kourami', 'Kourami', 'Kourami', 'Kourami', 'HLA-LA', 'HLA-LA',  'HLA-LA', 'HLA-LA', 'Optitype', 'Optitype', 'Optitype', 'Optitype', 'Hisatgenotype','Hisatgenotype', 'Hisatgenotype','Hisatgenotype', 'STC-seq', 'STC-seq', 'STC-seq', 'STC-seq', 'ensemble_all', 'ensemble_all', 'ensemble_all', 'ensemble_all', 'ensemble_graph', 'ensemble_graph', 'ensemble_graph', 'ensemble_graph', 'Total', 'Total', 'Total']
measure_list = ['score', 'count', 'call_rate', 'accuracy', 'score', 'count', 'call_rate', 'accuracy','score', 'count', 'call_rate', 'accuracy','score', 'count', 'call_rate', 'accuracy','score', 'count', 'call_rate', 'accuracy','score', 'count', 'call_rate', 'accuracy', 'score', 'count', 'call_rate', 'accuracy', 'count']

arrays = [tool_extended_list,measure_list]
tuples = list(zip(*arrays))

index = pd.MultiIndex.from_tuples(tuples, names=['Tool', 'Metric'])

#Make overall dataframe: (Evaxion is HLA-I + DRB1)
results_df = pd.DataFrame(0, index=['A', 'B', 'C', 'DRB1', 'DQB1', 'HLA-I', 'HLA-II', 'Evaxion', 'Total'], columns=index)

#Loop over subjects:
for subject in list(MG_exome_merged_df.index):
    
    #Only include subjects which have been typed by the tools:
    if subject not in gold_standard_id_list:
        continue
      
    #Loop over alleles
    for allele in MG_exome_merged_df.columns[1:]:
        results_df.loc[allele, idx['Total', 'count']] += 2
        
        facit = MG_exome_merged_df.loc[subject,allele]

        
        results_df.loc[allele, idx['Kourami', 'score']]  += check_result(facit, kourami_results, subject, 'Kourami', allele)
        results_df.loc[allele, idx['Kourami', 'count']]  += get_count(allele, kourami_results, subject)
      
 
        results_df.loc[allele, idx['HLA-LA', 'score']]+= check_result(facit, hla_la_results, subject, 'HLA-LA', allele)
        results_df.loc[allele, idx['HLA-LA', 'count']]+= get_count(allele, hla_la_results, subject)

    
        results_df.loc[allele, idx['Optitype', 'score']] += check_result(facit, optitype_results, subject, 'Optitype', allele)
        results_df.loc[allele, idx['Optitype', 'count']]+= get_count(allele, optitype_results, subject)
        
        
        results_df.loc[allele, idx['Hisatgenotype', 'score']] += check_result(facit, hisatgenotype_results, subject, 'Hisatgenotype', allele)
        results_df.loc[allele, idx['Hisatgenotype', 'count']]+= get_count(allele, hisatgenotype_results, subject)
        
        
        results_df.loc[allele, idx['STC-seq', 'score']] += check_result(facit, stc_seq_results, subject, 'STC-seq', allele)
        results_df.loc[allele, idx['STC-seq', 'count']]+= get_count(allele, stc_seq_results, subject)
        
        #The majority vote methods:
        
        results_df.loc[allele, idx['ensemble_all', 'score']] += check_result(facit, all_five_results, subject, 'ensemble_all', allele)
        results_df.loc[allele, idx['ensemble_all', 'count']]+= get_count(allele, all_five_results, subject)
        
        
        results_df.loc[allele, idx['ensemble_graph', 'score']] += check_result(facit, graph_tools_results, subject, 'ensemble_graph', allele)
        results_df.loc[allele, idx['ensemble_graph', 'count']]+= get_count(allele, graph_tools_results, subject)

NA06985
Kourami ['A*03:01:01G', 'A*02:01:01G', 'B*07:02:01G', 'B*07:235', 'C*07:02:01G', 'C*06:02:01G', 'DQB1*06:02:01G', 'DQB1*06:02:01G', 'DRB1*15:01:01G', 'DRB1*15:01:01G']
[['B*07:02:01'], ['B*57:01']]


NA06985
HLA-LA ['A*02:01:01G', 'A*03:01:01G', 'B*07:02:01G', 'B*57:01:01G', 'C*06:02:01G', 'C*07:02:01G', 'DQB1*06:02:01G', 'DQB1*06:02:01G', 'DRB1*15:01:01G', 'DRB1*15:01:01G']
[['B*07:02:01'], ['B*57:01']]


NA06985
Optitype ['A*03:01', 'A*02:01', 'B*57:01', 'B*07:02', 'C*06:02', 'C*07:02']
[['B*07:02:01'], ['B*57:01']]


NA06985
Hisatgenotype ['A*02:01:01:10', 'A*03:01:01:10', 'B*07:02:01', 'B*57:01:01', 'C*06:02:01:01', 'C*07:02:01:03', 'DQB1*06:02:01:01', 'DQB1*06:02:01:01', 'DRB1*15:01:01:01', 'DRB1*15:01:01:03']
[['B*07:02:01'], ['B*57:01']]


NA06985
STC-seq ['A*02:01:01', 'A*03:01:01', 'B*07:02:01', 'B*07:02:06', 'C*06:116N', 'C*07:02:01', 'DQB1*06:02:01', 'DQB1*06:02:01', 'DRB1*15:01:01', 'DRB1*15:01:01']
[['B*07:02:01'], ['B*57:01']]


NA06985
ensemble_all ['A*02:01:01G'

NA06994
Hisatgenotype ['A*32:01:01', 'A*02:01:01:01', 'B*08:01:01:01', 'B*40:02:01', 'C*02:02:02:01', 'C*07:01:01:02', 'DRB1*01:01:01', 'DRB1*04:04:01', 'DQB1*03:02:01:01', 'DQB1*05:01:01:01']
[['DRB1*01:01'], ['DRB1*04:04']]


NA06994
STC-seq ['A*02:01:01', 'A*32:01:01', 'B*08:01:01', 'B*40:02:01', 'DQB1*03:02:01', 'DQB1*05:01:01', 'DRB1*01:01:01', 'DRB1*04:08:01']
[['DRB1*01:01'], ['DRB1*04:04']]


NA06994
ensemble_all ['A*02:01:01G', 'A*32:01:01G', 'B*08:01:01G', 'B*40:02:01G', 'C*02:02:02G', 'C*07:01:01G', 'DRB1*01:01:01G', 'DRB1*04:04:01', 'DQB1*03:02:01G', 'DQB1*05:01:01G']
[['DRB1*01:01'], ['DRB1*04:04']]


NA06994
ensemble_graph ['A*02:01:01G', 'A*32:01:01G', 'B*08:01:01G', 'B*40:02:01G', 'C*02:02:02G', 'C*07:01:01G', 'DRB1*01:01:01G', 'DRB1*04:04:01', 'DQB1*03:02:01G', 'DQB1*05:01:01G']
[['DRB1*01:01'], ['DRB1*04:04']]


NA06994
Kourami ['A*32:01:01G', 'A*02:01:01G', 'B*08:01:01G', 'B*40:02:01G', 'C*02:02:02G', 'C*07:01:01G', 'DQB1*05:01:01G', 'DQB1*03:02:01G', 'DRB1*01:01:01G

NA07048
STC-seq ['A*02:425', 'A*02:425', 'B*07:02:13', 'B*07:93', 'C*07:02:01', 'C*07:307', 'DQB1*06:02:01', 'DQB1*06:02:01', 'DRB1*04:13', 'DRB1*04:73']
[['C*05:01'], ['C*07:02']]


NA07048
ensemble_all ['A*02:01:01G', 'A*02:01:01G', 'B*07:02:01G', 'B*44:02:01G', 'C*05:01:01G', 'C*07:02:01G', 'DRB1*04:01:01', 'DRB1*15:01:01G', 'DQB1*06:02:01G', 'DQB1*06:139']
[['C*05:01'], ['C*07:02']]


NA07048
ensemble_graph ['A*02:01:01G', 'A*02:01:01G', 'B*07:02:01G', 'B*44:02:01G', 'C*05:01:01G', 'C*07:02:01G', 'DRB1*04:01:01', 'DRB1*15:01:01G', 'DQB1*06:02:01G', 'DQB1*06:139']
[['C*05:01'], ['C*07:02']]


NA07048
Kourami ['A*02:01:01G', 'A*02:01:01G', 'B*07:02:01G', 'B*44:02:01G', 'C*05:01:01G', 'C*07:02:01G', 'DQB1*06:139', 'DQB1*06:02:01G', 'DRB1*04:01:01', 'DRB1*15:01:01G']
[['DRB1*04:01'], ['DRB1*15:01']]


NA07048
HLA-LA ['A*02:01:01G', 'A*02:01:01G', 'B*07:02:01G', 'B*44:02:01G', 'C*05:01:01G', 'C*07:02:01G', 'DQB1*03:01:01G', 'DQB1*06:02:01G', 'DRB1*04:01:01', 'DRB1*15:01:01G']
[['DRB1*04

NA07056
ensemble_graph ['A*01:01:01G', 'A*02:01:01G', 'B*08:01:01G', 'B*57:31', 'C*06:02:01G', 'C*07:01:01G', 'DRB1*03:01:01G', 'DRB1*07:01:01G', 'DQB1*02:01:01G', 'DQB1*03:03:02G']
[['DQB1*02:01'], ['DQB1*03:03']]


NA07347
Kourami ['A*30:02:01G', 'A*26:01:01G', 'B*44:02:01G', 'B*18:01:01G', 'C*05:01:01G', 'C*05:01:01G', 'DQB1*02:01:01G', 'DQB1*03:01:01G', 'DRB1*11:04:01G', 'DRB1*03:01:01G']
[['B*18:01'], ['B*44:02']]


NA07347
HLA-LA ['A*26:01:01G', 'A*30:02:01G', 'B*18:01:01G', 'B*44:02:01G', 'C*05:01:01G', 'C*05:01:01G', 'DQB1*03:01:01G', 'DQB1*02:01:01G', 'DRB1*11:04:01G', 'DRB1*03:01:01G']
[['B*18:01'], ['B*44:02']]


NA07347
Hisatgenotype ['A*30:02:01:01', 'A*26:14', 'B*18:01:01:01', 'B*44:02:01:01', 'C*05:01:01:02', 'C*05:01:01:01', 'DRB1*03:01:01:02', 'DRB1*11:04:01', 'DQB1*03:01:01:03', 'DQB1*02:01:01']
[['B*18:01'], ['B*44:02']]


NA07347
STC-seq ['C*05:53', 'C*05:53', 'DRB1*11:136', 'DRB1*11:136']
[['B*18:01'], ['B*44:02']]


NA07347
ensemble_all ['A*26:01:01G', 'A*30:02:01

NA10851
Hisatgenotype ['A*01:01:01:04', 'A*24:02:01:01', 'B*08:01:01:01', 'B*40:01:02', 'C*03:04:01:01', 'C*07:01:01:01', 'DRB1*04:04:01', 'DRB1*07:01:01:01', 'DQB1*03:02:01:02', 'DQB1*03:03:02:04']
[['B*40:01'], ['B*08:01']]


NA10851
STC-seq ['A*01:01:01', 'A*24:02:01', 'B*08:01:01', 'B*40:01:02', 'DQB1*03:02:01', 'DQB1*03:03:02', 'DRB1*04:04:01', 'DRB1*07:01:01']
[['B*40:01'], ['B*08:01']]


NA10851
ensemble_all ['A*01:01:01G', 'A*24:02:01G', 'B*08:01:01G', 'B*40:01:01G', 'C*03:04:01G', 'C*07:01:01G', 'DRB1*04:04:01', 'DRB1*07:01:01G', 'DQB1*03:02:01G', 'DQB1*03:03:02G']
[['B*40:01'], ['B*08:01']]


NA10851
ensemble_graph ['A*01:01:01G', 'A*24:02:01G', 'B*08:01:01G', 'B*40:01:01G', 'C*03:04:01G', 'C*07:01:01G', 'DRB1*04:04:01', 'DRB1*07:01:01G', 'DQB1*03:02:01G', 'DQB1*03:03:02G']
[['B*40:01'], ['B*08:01']]


NA10851
Kourami ['A*01:01:01G', 'A*24:02:01G', 'B*08:01:01G', 'B*40:01:01G', 'C*03:04:01G', 'C*07:01:01G', 'DQB1*03:03:02G', 'DQB1*03:02:01G', 'DRB1*04:04:01', 'DRB1*07:01:01G'

...

HG01551
ensemble_graph ['A*29:02:01G', 'A*33:03:01G', 'B*07:05:01G', 'B*15:16:01G', 'C*14:02:01G', 'C*15:05:01G', 'DRB1*01:02:01', 'DRB1*11:01:02', 'DQB1*03:01:01G', 'DQB1*05:01:01G']
[['B*07:05:01', 'B*07:06'], ['B*15:16']]


HG01551
Kourami ['A*33:03:01G', 'A*29:02:01G', 'B*07:05:01G', 'B*15:16:01G', 'C*15:05:01G', 'C*14:02:01G', 'DQB1*05:01:01G', 'DQB1*03:01:01G', 'DRB1*01:02:01', 'DRB1*11:01:02']
[['C*14:02:01'], ['C*15:05:01', 'C*15:05:02', 'C*15:05:03']]


HG01551
HLA-LA ['A*33:03:01G', 'A*29:02:01G', 'B*07:05:01;B*07:06', 'B*15:16:01', 'C*14:02:01G', 'C*15:05:01G', 'DQB1*03:01:01G', 'DQB1*05:01:01G', 'DRB1*01:02:01G', 'DRB1*11:01:02']
[['C*14:02:01'], ['C*15:05:01', 'C*15:05:02', 'C*15:05:03']]


HG01551
Optitype ['A*33:03', 'A*29:02', 'B*07:05', 'B*15:16', 'C*14:02', 'C*15:05']
[['C*14:02:01'], ['C*15:05:01', 'C*15:05:02', 'C*15:05:03']]


HG01551
Hisatgenotype ['A*33:03:01', 'A*29:02:01:01', 'B*07:06:01', 'B*15:16:01:02', 'C*14:02:01:01', 'C*15:05:02', 'DRB1*01:02:01', 'DRB1*1

NA19223
Kourami ['A*30:01:01G', 'A*33:03:01G', 'C*17:01:01G', 'C*17:01:01G', 'DQB1*02:01:01G', 'DQB1*04:02:01G', 'DRB1*03:02:01', 'DRB1*13:27']
[['DQB1*04:02', 'DQB1*02:01:01', 'DQB1*02:02', 'DQB1*02:04'], ['DQB1*02:01', 'DQB1*04:02']]


NA19223
HLA-LA ['A*30:01:01G', 'A*33:03:01G', 'B*41:04', 'B*42:01:01G', 'C*17:01:01G', 'C*17:01:01G', 'DQB1*04:02:01G', 'DQB1*02:01:01G', 'DRB1*03:02:01', 'DRB1*13:27']
[['DQB1*04:02', 'DQB1*02:01:01', 'DQB1*02:02', 'DQB1*02:04'], ['DQB1*02:01', 'DQB1*04:02']]


NA19223
Optitype ['A*30:01', 'A*33:03', 'B*42:01', 'B*41:02', 'C*17:01', 'C*17:01']
[['DQB1*04:02', 'DQB1*02:01:01', 'DQB1*02:02', 'DQB1*02:04'], ['DQB1*02:01', 'DQB1*04:02']]


NA19223
Hisatgenotype ['A*30:01:01', 'A*33:78', 'B*41:02:01', 'B*42:01:01', 'C*17:01:01:02', 'C*17:01:01:02', 'DQB1*02:01:01', 'DQB1*04:02:01', 'DRB1*03:02:03', 'DRB1*13:27']
[['DQB1*04:02', 'DQB1*02:01:01', 'DQB1*02:02', 'DQB1*02:04'], ['DQB1*02:01', 'DQB1*04:02']]


NA19223
STC-seq ['A*30:01:01', 'A*33:03:01', 'B*41:0

HG01873
Optitype ['A*02:03', 'A*03:01', 'B*35:03', 'B*55:02', 'C*04:01', 'C*12:03']
[['DQB1*04:02'], ['DQB1*05:03']]


HG01873
Hisatgenotype ['A*02:03:01', 'A*03:01:01:01', 'B*35:03:01:01', 'B*55:02:01:01', 'C*04:01:01:01', 'C*12:03:01:06', 'DRB1*08:02:01', 'DRB1*14:05:01', 'DQB1*05:03:01:02', 'DQB1*04:02:01']
[['DQB1*04:02'], ['DQB1*05:03']]


HG01873
STC-seq []
[['DQB1*04:02'], ['DQB1*05:03']]


HG01873
ensemble_all ['A*02:03:01G', 'A*03:01:01G', 'B*35:60', 'B*56:11', 'C*04:01:01G', 'C*12:03:01G', 'DRB1*08:02:01', 'DRB1*14:05:01', 'DQB1*04:02:01G', 'DQB1*05:03:01G']
[['DQB1*04:02'], ['DQB1*05:03']]


HG01873
ensemble_graph ['A*02:03:01G', 'A*03:01:01G', 'B*35:60', 'B*56:11', 'C*04:01:01G', 'C*12:03:01G', 'DRB1*08:02:01', 'DRB1*14:05:01', 'DQB1*04:02:01G', 'DQB1*05:03:01G']
[['DQB1*04:02'], ['DQB1*05:03']]


HG01886
Kourami ['A*74:01:01G', 'A*30:02:01G', 'B*15:03:01G', 'B*57:03:01G', 'C*02:10:01G', 'C*07:01:01G', 'DQB1*05:02:01G', 'DQB1*06:09:01G', 'DRB1*11:01:02', 'DRB1*13:02:01G']
[

HG01872
ensemble_all ['A*11:02:01G', 'A*24:07:01', 'B*27:04:01G', 'B*39:05:01', 'C*08:01:01G', 'C*12:02:01G', 'DRB1*08:03:02', 'DRB1*12:02:01', 'DQB1*03:01:01G', 'DQB1*06:01:01G']
[['DQB1*03:01'], ['DQB1*06:01']]


HG01872
ensemble_graph ['A*11:02:01G', 'A*24:07:01', 'B*27:04:01G', 'B*39:05:01', 'C*08:01:01G', 'C*12:02:01G', 'DRB1*08:03:02', 'DRB1*12:02:01', 'DQB1*03:01:01G', 'DQB1*06:01:01G']
[['DQB1*03:01'], ['DQB1*06:01']]


HG01757
Kourami ['A*01:01:01G', 'A*02:01:01G', 'B*57:01:01G', 'B*18:01:01G', 'C*07:01:01G', 'C*07:01:01G', 'DQB1*03:03:02G', 'DQB1*02:01:01G', 'DRB1*03:01:01G', 'DRB1*07:01:01G']
[['B*18:01'], ['B*57:01']]


HG01757
HLA-LA ['A*01:01:01G', 'A*02:01:01G', 'B*18:01:01G', 'B*57:01:01G', 'C*07:01:01G', 'C*07:01:01G', 'DQB1*02:01:01G', 'DQB1*03:03:02G', 'DRB1*03:01:01G', 'DRB1*07:01:01G']
[['B*18:01'], ['B*57:01']]


HG01757
Hisatgenotype ['A*01:01:01:01', 'A*02:01:01:05', 'B*57:01:01', 'B*18:01:01:02', 'C*07:01:01:01', 'C*07:01:01:02', 'DRB1*03:01:01:01', 'DRB1*07:01

NA20313
ensemble_all ['A*03:01:01G', 'A*68:02:01G', 'B*35:01:01G', 'B*53:01:01G', 'C*04:01:01G', 'C*04:01:01G', 'DRB1*04:05:01', 'DRB1*08:04:01', 'DQB1*03:01:01G', 'DQB1*03:02:01G']
[['B*35:01'], ['B*53:01']]


NA20313
ensemble_graph ['A*03:01:01G', 'A*68:02:01G', 'B*35:01:01G', 'B*53:01:01G', 'C*04:01:01G', 'C*04:01:01G', 'DRB1*04:05:01', 'DRB1*08:04:01', 'DQB1*03:01:01G', 'DQB1*03:02:01G']
[['B*35:01'], ['B*53:01']]


NA20313
Kourami ['A*03:01:01G', 'A*68:02:01G', 'B*35:01:01G', 'B*53:01:01G', 'C*04:01:01G', 'C*04:01:01G', 'DQB1*03:02:01G', 'DQB1*03:01:01G', 'DRB1*04:05:01', 'DRB1*08:04:01']
[['C*04:01'], ['C*04:01']]


NA20313
HLA-LA ['A*03:01:01G', 'A*68:02:01G', 'B*35:01:01G', 'B*53:01:01G', 'C*04:01:01G', 'C*04:01:01G', 'DQB1*03:01:01G', 'DQB1*03:02:01G', 'DRB1*04:05:01', 'DRB1*08:04:01']
[['C*04:01'], ['C*04:01']]


NA20313
Hisatgenotype ['A*03:01:01:05', 'A*68:02:01:01', 'B*35:01:01:03', 'B*53:01:01', 'C*04:01:01:01', 'C*04:01:01:01', 'DQB1*03:01:01:03', 'DQB1*03:02:01:01', 'DR

In [33]:
#Calculate counts for Total:
#Add for Total:
results_df.loc['HLA-I', idx['Total', 'count']] += sum(results_df.loc[['A','B','C'], idx['Total', 'count']])
results_df.loc['HLA-II', idx['Total', 'count']] += sum(results_df.loc[['DRB1','DQB1'], idx['Total', 'count']])
results_df.loc['Evaxion', idx['Total', 'count']] += sum(results_df.loc[['HLA-I','DRB1'], idx['Total', 'count']])
results_df.loc['Total', idx['Total', 'count']] += sum(results_df.loc[['HLA-I','HLA-II'], idx['Total', 'count']])


#Loop over subjects:
for method in ['HLA-LA', 'Hisatgenotype', 'Kourami', 'Optitype', 'STC-seq', 'ensemble_all', 'ensemble_graph']:
    
    #Calculate scores for groups of alleles:
    results_df.loc['HLA-I', idx[method, 'score']] += sum(results_df.loc[['A','B','C'], idx[method, 'score']])
    results_df.loc['HLA-II', idx[method, 'score']] += sum(results_df.loc[['DRB1','DQB1'], idx[method, 'score']])
    results_df.loc['Evaxion', idx[method, 'score']] += sum(results_df.loc[['HLA-I','DRB1'], idx[method, 'score']])
    results_df.loc['Total', idx[method, 'score']] += sum(results_df.loc[['HLA-I','HLA-II'], idx[method, 'score']])
         
    results_df.loc['HLA-I', idx[method, 'count']] += sum(results_df.loc[['A','B','C'], idx[method, 'count']])
    results_df.loc['HLA-II', idx[method, 'count']] += sum(results_df.loc[['DRB1','DQB1'], idx[method, 'count']])
    results_df.loc['Evaxion', idx[method, 'count']] += sum(results_df.loc[['HLA-I','DRB1'], idx[method, 'count']])
    results_df.loc['Total', idx[method, 'count']] += sum(results_df.loc[['HLA-I','HLA-II'], idx[method, 'count']])
                                                        
        
    for gene in list(results_df.index):

        results_df.loc[gene, idx[method, 'call_rate']] += round(results_df.loc[gene, idx[method, 'count']] / results_df.loc[gene, idx['Total', 'count']]*100,2)
        
        results_df.loc[gene, idx[method, 'accuracy']] += round(results_df.loc[gene, idx[method, 'score']] / results_df.loc[gene, idx['Total', 'count']]*100,2)
        
        

C:\Users\nikol\Anaconda3\lib\site-packages\ipykernel_launcher.py:26: RuntimeWarning: invalid value encountered in longlong_scalars
C:\Users\nikol\Anaconda3\lib\site-packages\ipykernel_launcher.py:28: RuntimeWarning: invalid value encountered in double_scalars
C:\Users\nikol\Anaconda3\lib\site-packages\ipykernel_launcher.py:26: RuntimeWarning: invalid value encountered in double_scalars


In [34]:
results_df

Tool    Kourami                            HLA-LA                           \
Metric    score   count call_rate accuracy  score count call_rate accuracy   
A           0.0     0.0       NaN      NaN      0     0       NaN      NaN   
B          75.0  1436.0     86.61     4.52    154  1658     100.0     9.29   
C          24.0  1504.0     90.71     1.45     34  1658     100.0     2.05   
DRB1      297.0  1648.0     99.40    17.91    353  1658     100.0    21.29   
DQB1        2.0  1388.0     83.72     0.12      0  1658     100.0     0.00   
HLA-I      99.0  2940.0     88.66     2.99    188  3316     100.0     5.67   
HLA-II    299.0  3036.0     91.56     9.02    353  3316     100.0    10.65   
Evaxion   396.0  4588.0     92.24     7.96    541  4974     100.0    10.88   
Total     398.0  5976.0     90.11     6.00    541  6632     100.0     8.16   

Tool    Optitype                            Hisatgenotype                    \
Metric     score   count call_rate accuracy         score   count call_rate   
A            0.0     0.0       NaN      NaN           0.0     0.0       NaN   
B          431.0  1658.0    100.00    26.00         647.0  1658.0     100.0   
C          323.0  1658.0    100.00    19.48         721.0  1658.0     100.0   
DRB1         0.0     0.0      0.00     0.00         786.0  1658.0     100.0   
DQB1         0.0     0.0      0.00     0.00         272.0  1658.0     100.0   
HLA-I      754.0  3316.0    100.00    22.74        1368.0  3316.0     100.0   
HLA-II       0.0     0.0      0.00     0.00        1058.0  3316.0     100.0   
Evaxion    754.0  3316.0     66.67    15.16        2154.0  4974.0     100.0   
Total      754.0  3316.0     50.00    11.37        2426.0  6632.0     100.0   

Tool             STC-seq                            ensemble_all          \
Metric  accuracy   score   count call_rate accuracy        score   count   
A            NaN     0.0     0.0       NaN      NaN          0.0     0.0   
B          39.02   457.0  1180.0     71.17    27.56        172.0  1658.0   
C          43.49   262.0  1126.0     67.91    15.80        107.0  1658.0   
DRB1       47.41   531.0  1280.0     77.20    32.03        349.0  1658.0   
DQB1       16.41   492.0   960.0     57.90    29.67         39.0  1658.0   
HLA-I      41.25   719.0  2306.0     69.54    21.68        279.0  3316.0   
HLA-II     31.91  1023.0  2240.0     67.55    30.85        388.0  3316.0   
Evaxion    43.31  1250.0  3586.0     72.09    25.13        628.0  4974.0   
Total      36.58  1742.0  4546.0     68.55    26.27        667.0  6632.0   

Tool                       ensemble_graph                            Total  
Metric  call_rate accuracy          score   count call_rate accuracy count  
A             NaN      NaN            0.0     0.0       NaN      NaN     0  
B           100.0    10.37           97.0  1658.0     100.0     5.85  1658  
C           100.0     6.45           29.0  1658.0     100.0     1.75  1658  
DRB1        100.0    21.05          347.0  1658.0     100.0    20.93  1658  
DQB1        100.0     2.35            2.0  1658.0     100.0     0.12  1658  
HLA-I       100.0     8.41          126.0  3316.0     100.0     3.80  3316  
HLA-II      100.0    11.70          349.0  3316.0     100.0    10.52  3316  
Evaxion     100.0    12.63          473.0  4974.0     100.0     9.51  4974  
Total       100.0    10.06          475.0  6632.0     100.0     7.16  6632

# Add metadata to error dataframe

In [35]:
#Join the error dataframe with information of continent and ethnicity
errors_with_metadata_hla_I_df_1 = error_dataframe_hla_I.join(m2018_gs_raw_df[['Region', 'sbgroup']])
errors_with_metadata_hla_I_df_1.rename(columns={'sbgroup' : 'Population'}, inplace=True)

#The same for HLA-II
errors_with_metadata_hla_II_df_1 = error_dataframe_hla_II.join(m2018_gs_raw_df[['Region', 'sbgroup']])
errors_with_metadata_hla_II_df_1.rename(columns={'sbgroup' : 'Population'}, inplace=True)

NameError: name 'm2018_gs_raw_df' is not defined

In [ ]:
#Datapath for metadata excelsheet:
metadata_path = gold_standard_path + '1000G_sample_info.xlsx'

#Load data for gender and translation of Population abbreviations
metadata_1_df = pd.read_excel(metadata_path, sheet_name='Sample Info')[['Sample', 'Population', 'Population Description', 'Gender']]

#load data for sequencing center:
metadata_2_df = pd.read_excel(metadata_path, sheet_name='Final Phase Sequence Data')[['Unnamed: 0', 'Exome']]

#Reset header in metadata_2
new_header = metadata_2_df.iloc[0] #grab the first row for the header
metadata_2_df = metadata_2_df[1:] #take the data less the header row
metadata_2_df.columns = new_header #set the header row as the df header

#Set "Sample" as inde in both metadata dataframes:
metadata_1_df.set_index('Sample', inplace=True)
metadata_2_df.set_index('Sample', inplace=True)

In [ ]:
#Join the relevant info to the error dataframe:
errors_with_metadata_hla_I_df_2 = errors_with_metadata_hla_I_df_1.join(metadata_1_df[['Population Description', 'Gender']])

errors_metadata_hla_I_df = errors_with_metadata_hla_I_df_2.join(metadata_2_df[['Center']])

#Do the same for HLA-II
errors_with_metadata_hla_II_df_2 = errors_with_metadata_hla_II_df_1.join(metadata_1_df[['Population Description', 'Gender']])

errors_metadata_hla_II_df = errors_with_metadata_hla_II_df_2.join(metadata_2_df[['Center']])

### Add a column with the sum of errors for all but STC-seq

In [ ]:
errors_metadata_hla_I_df['mean_error_graph'] = errors_metadata_hla_I_df.apply(lambda row: (row['Kourami'] + row['HLA-LA'] + row['Hisatgenotype']) / 3  , axis = 1) 

errors_metadata_hla_II_df['mean_error_graph'] = errors_metadata_hla_II_df.apply(lambda row: (row['Kourami'] + row['HLA-LA'] + row['Hisatgenotype']) / 3  , axis = 1) 


# Plots of the Performance of the tools

In [ ]:
#labels in order:
labels = ['Kourami', 'HLA-LA', 'Optitype', 'Hisatgenotype', 'STC-seq', 'ensemble_all', 'ensemble_graph']

def make_plot_from_allele_list(allele_index):

    if allele_index in ('HLA-II', 'DRB1', 'DQB1'):
        accuracy = list(results_df.loc[allele_index, idx[['Kourami', 'HLA-LA', 'Hisatgenotype', 'STC-seq', 'ensemble_graph'], 'accuracy']])
        call_rate = list(results_df.loc[allele_index, idx[['Kourami', 'HLA-LA', 'Hisatgenotype', 'STC-seq', 'ensemble_graph'], 'call_rate']])
        
        x = np.arange(len(labels)-2)
        
    else:
        accuracy = list(results_df.loc[allele_index, idx[:, 'accuracy']])
        call_rate = list(results_df.loc[allele_index, idx[:, 'call_rate']])
        
        x = np.arange(len(labels))  # the label locations
        

    
    width = 0.35  # the width of the bars

    fig, ax = plt.subplots(figsize=(10,6))
    rects1 = ax.bar(x - width/2, accuracy, width, label='accuracy', color = '#0000FF')
    rects2 = ax.bar(x + width/2, call_rate, width, label='call_rate', color = '#808080')

    # Add some text for labels, title and custom x-axis tick labels, etc.
    ax.set_ylabel('Score')
    ax.set_xticks(x)
    
    if allele_index in ('HLA-II', 'DRB1', 'DBQ1'):
        ax.set_xticklabels(['Kourami', 'HLA-LA', 'Hisatgenotype', 'STC-seq', 'ensemble_graph'], rotation = 45)
    else:
        ax.set_xticklabels(labels, rotation = 45)

    ax.legend()


    def autolabel(rects):
        """Attach a text label above each bar in *rects*, displaying its height."""
        for rect in rects:
            height = rect.get_height()
            ax.annotate('{}'.format(height),
                        xy=(rect.get_x() + rect.get_width() / 2, 10),
                        xytext=(0, 3),  # 3 points vertical offset
                        textcoords="offset points",
                        ha='center', va='bottom', 
                        color="w", size = 8, weight = 800)


    autolabel(rects1)
    autolabel(rects2)

    # Major ticks every 20, minor ticks every 5
    minor_ticks = np.arange(0, 101, 5)

    ax.set_yticks(minor_ticks, minor=True)

    ax.grid(which='minor', alpha=0.4)

    # Or if you want different settings for the grids:
    plt.grid(axis = 'y')
    ax.set_axisbelow(True)

    plt.legend(bbox_to_anchor=(1.05, 1.0), loc='upper left')
    plt.tight_layout()

    plt.title('HLA typing performance for allele: ' + allele_index)
    return plt, ax

## Overall Results

In [ ]:
make_plot_from_allele_list('Total')

## Evaxion Alleles (HLA-I + DRB1)

In [ ]:
make_plot_from_allele_list('Evaxion')

## HLA-I and HLA-II

In [ ]:
make_plot_from_allele_list('HLA-I')

In [ ]:
make_plot_from_allele_list('HLA-II')

## Individual Alleles

In [ ]:
make_plot_from_allele_list('A')

In [ ]:
make_plot_from_allele_list('B')

In [ ]:
make_plot_from_allele_list('C')

In [ ]:
make_plot_from_allele_list('DRB1')

In [ ]:
make_plot_from_allele_list('DQB1')

# Analysis of Errors in relation to sequencing depth

In [ ]:
kourami_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
optitype_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
hla_la_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
hisatgenotype_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
stc_seq_length_dist_df = pd.DataFrame(columns = ['mean_depth'])

for sample_id in list(error_dataframe_hla_I.index): 
    #Kourami
    n_errors = error_dataframe_hla_I.loc[sample_id, 'Kourami']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_I.loc[sample_id, 'mean_depth']
            kourami_length_dist_df = kourami_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)
    
    #Optitype
    n_errors = error_dataframe_hla_I.loc[sample_id, 'Optitype']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_I.loc[sample_id, 'mean_depth']
            optitype_length_dist_df = optitype_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)
            
    #HLA-LA
    n_errors = error_dataframe_hla_I.loc[sample_id, 'HLA-LA']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_I.loc[sample_id, 'mean_depth']
            hla_la_length_dist_df = hla_la_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)

    #Hisatgenotype
    n_errors = error_dataframe_hla_I.loc[sample_id, 'Hisatgenotype']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_I.loc[sample_id, 'mean_depth']
            hisatgenotype_length_dist_df = hisatgenotype_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)

    #STC-seq
    n_errors = error_dataframe_hla_I.loc[sample_id, 'STC-seq']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_I.loc[sample_id, 'mean_depth']
            stc_seq_length_dist_df = stc_seq_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)


In [ ]:
labels_boxplot = ['Full Dataset'] + labels[:-2]

overall_coverage = error_dataframe_hla_I['mean_depth'].values
kourami_coverage = kourami_length_dist_df['mean_depth'].values
optitype_coverage = optitype_length_dist_df['mean_depth'].values
hla_la_coverage= hla_la_length_dist_df['mean_depth'].values
hisatgenotype_coverage = hisatgenotype_length_dist_df['mean_depth'].values
stc_seq_coverage = stc_seq_length_dist_df['mean_depth'].values
data = [overall_coverage, kourami_coverage, hla_la_coverage, optitype_coverage, hisatgenotype_coverage, stc_seq_coverage] 
  
    
fig = plt.figure(figsize =(10, 7)) 
  
# Creating axes instance 
ax = fig.add_axes([0, 0, 1, 1]) 
 
# Creating plot 
bp = ax.boxplot(data) 
  
# show plot 
ax.set_xticklabels(labels_boxplot, rotation = 45)

ax.set_ylim(0, max(overall_coverage)+10)
 

## Doing these calculations might not be viable, as the distributions aren't normal. Maybe Kurtosis instead or transform distribution to normal first

In [ ]:
overall_mean = error_dataframe_hla_I['mean_depth'].mean()
kourami_mean = kourami_length_dist_df['mean_depth'].mean()
optitype_mean = optitype_length_dist_df['mean_depth'].mean()
hla_la_mean = hla_la_length_dist_df['mean_depth'].mean()
hisatgenotype_mean = hisatgenotype_length_dist_df['mean_depth'].mean()
stc_seq_mean = stc_seq_length_dist_df['mean_depth'].mean()

mean_values = [overall_mean, kourami_mean, optitype_mean, hla_la_mean, hisatgenotype_mean, stc_seq_mean]

overall_std = error_dataframe_hla_I['mean_depth'].std()
kourami_std = kourami_length_dist_df['mean_depth'].std()
optitype_std = optitype_length_dist_df['mean_depth'].std()
hla_la_std = hla_la_length_dist_df['mean_depth'].std()
hisatgenotype_std = hisatgenotype_length_dist_df['mean_depth'].std()
stc_seq_std = stc_seq_length_dist_df['mean_depth'].std()

std_values = [overall_std, kourami_std, optitype_std, hla_la_std, hisatgenotype_std, stc_seq_std]

plt.bar(range(len(error_dataframe_hla_I.columns[:-2])), mean_values, 
        yerr=std_values, align='center', alpha=0.5, color = '#0000FF')

plt.xticks(range(len(error_dataframe_hla_I.columns[:-2])), ['All Samples'] + list(error_dataframe_hla_I.columns[1:-2]), rotation = 45)
plt.ylabel('depth')
plt.title('Mean Sequencing coverage with std. error')
plt.show()

# The same analysis - now for HLA-II

In [ ]:
kourami_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
optitype_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
hla_la_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
hisatgenotype_length_dist_df = pd.DataFrame(columns = ['mean_depth'])
stc_seq_length_dist_df = pd.DataFrame(columns = ['mean_depth'])

for sample_id in list(error_dataframe_hla_II.index): 
    #Kourami
    n_errors = error_dataframe_hla_II.loc[sample_id, 'Kourami']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_II.loc[sample_id, 'mean_depth']
            kourami_length_dist_df = kourami_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)
    
    #HLA-LA
    n_errors = error_dataframe_hla_II.loc[sample_id, 'HLA-LA']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_II.loc[sample_id, 'mean_depth']
            hla_la_length_dist_df = hla_la_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)

    #Hisatgenotype
    n_errors = error_dataframe_hla_II.loc[sample_id, 'Hisatgenotype']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_II.loc[sample_id, 'mean_depth']
            hisatgenotype_length_dist_df = hisatgenotype_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)

    #STC-seq
    n_errors = error_dataframe_hla_II.loc[sample_id, 'STC-seq']
    if n_errors > 0:
        for n in range(n_errors):
            depth_of_error_sample = error_dataframe_hla_II.loc[sample_id, 'mean_depth']
            stc_seq_length_dist_df = stc_seq_length_dist_df.append({'mean_depth' : depth_of_error_sample}, ignore_index=True)


In [ ]:
labels_boxplot = ['Full Dataset'] + labels[:-2]

overall_coverage = error_dataframe_hla_II['mean_depth'].values
kourami_coverage = kourami_length_dist_df['mean_depth'].values
hla_la_coverage= hla_la_length_dist_df['mean_depth'].values
hisatgenotype_coverage = hisatgenotype_length_dist_df['mean_depth'].values
stc_seq_coverage = stc_seq_length_dist_df['mean_depth'].values
data = [overall_coverage, kourami_coverage, hla_la_coverage, hisatgenotype_coverage, stc_seq_coverage] 
  
    
fig = plt.figure(figsize =(10, 7)) 
  
# Creating axes instance 
ax = fig.add_axes([0, 0, 1, 1]) 
 
# Creating plot 
bp = ax.boxplot(data) 
  
# show plot 
ax.set_xticklabels(labels_boxplot, rotation = 45)

ax.set_ylim(0, max(overall_coverage)+10)
 

In [ ]:
overall_mean = error_dataframe_hla_II['mean_depth'].mean()
kourami_mean = kourami_length_dist_df['mean_depth'].mean()
hla_la_mean = hla_la_length_dist_df['mean_depth'].mean()
hisatgenotype_mean = hisatgenotype_length_dist_df['mean_depth'].mean()
stc_seq_mean = stc_seq_length_dist_df['mean_depth'].mean()

mean_values = [overall_mean, kourami_mean, hla_la_mean, hisatgenotype_mean, stc_seq_mean]

overall_std = error_dataframe_hla_II['mean_depth'].std()
kourami_std = kourami_length_dist_df['mean_depth'].std()
hla_la_std = hla_la_length_dist_df['mean_depth'].std()
hisatgenotype_std = hisatgenotype_length_dist_df['mean_depth'].std()
stc_seq_std = stc_seq_length_dist_df['mean_depth'].std()

std_values = [overall_std, kourami_std, hla_la_std, hisatgenotype_std, stc_seq_std]

plt.bar(range(len(error_dataframe_hla_II.columns[:-2])), mean_values, 
        yerr=std_values, align='center', alpha=0.5, color = '#0000FF')

plt.xticks(range(len(error_dataframe_hla_II.columns[:-2])), ['All Samples'] + list(error_dataframe_hla_II.columns[1:-2]), rotation = 45)
plt.ylabel('depth')
plt.title('Mean Sequencing coverage with std. error')
plt.show()

# Errors in relation to gender and ethnicity

In [ ]:
labels_no_stc = ['Kourami', 'HLA-LA', 'Optitype', 'Hisatgenotype']

errors_metadata_hla_I_df[labels_no_stc+ ['mean_error_graph'] +['Region']].groupby(['Region']).agg([np.mean, np.std]) 

In [ ]:
labels_no_stc_no_optitype = ['Kourami', 'HLA-LA', 'Hisatgenotype'] 

errors_metadata_hla_II_df[labels_no_stc_no_optitype + ['mean_error_graph'] + ['Region']].groupby(['Region']).agg([np.mean, np.std])

### Overall analysis - mean performance of HISAT-genotype, Kourami and HLA-LA

In [ ]:
errors_metadata_hla_I_df[['mean_error_graph']+['Region']].groupby(['Region']).mean().unstack().plot(kind='bar')

In [ ]:
errors_metadata_hla_II_df[['mean_error_graph']+['Region']].groupby(['Region']).mean().unstack().plot(kind='bar')

In [ ]:
errors_metadata_hla_I_df[['mean_error_graph']+['Population']].groupby(['Population']).mean().unstack().plot(kind='bar')

In [ ]:
errors_metadata_hla_II_df[['mean_error_graph']+['Population']].groupby(['Population']).mean().unstack().plot(kind='bar')

In [ ]:
errors_metadata_hla_I_df[['mean_error_graph']+['Gender']].groupby(['Gender']).agg([np.mean, np.std])

In [ ]:
errors_metadata_hla_II_df[['mean_error_graph']+['Gender']].groupby(['Gender']).agg([np.mean, np.std])

In [ ]:
 errors_metadata_hla_I_df[['mean_error_graph']+['Gender']].groupby(['Gender']).mean().unstack().plot(kind='bar')

In [ ]:
 errors_metadata_hla_II_df[['mean_error_graph']+['Gender']].groupby(['Gender']).mean().unstack().plot(kind='bar')

### Over Kourami, HLA-LA, Optitype and HISAT-genotype individually:

In [ ]:
 errors_metadata_hla_I_df[labels_no_stc+['Region']].groupby(['Region']).mean().unstack().plot(kind='bar', figsize = (10,6))

In [ ]:
 errors_metadata_hla_II_df[labels_no_stc_no_optitype+['Region']].groupby(['Region']).mean().unstack().plot(kind='bar', figsize = (10,6))

In [ ]:
 errors_metadata_hla_I_df[labels_no_stc+['Population']].groupby(['Population']).mean().unstack().plot(kind='bar', figsize = (10,6))

In [ ]:
 errors_metadata_hla_II_df[labels_no_stc_no_optitype+['Population']].groupby(['Population']).mean().unstack().plot(kind='bar', figsize = (10,6))

In [ ]:
 errors_metadata_hla_I_df[labels_no_stc+['Gender']].groupby(['Gender']).agg([np.mean, np.std])

In [ ]:
errors_metadata_hla_II_df[labels_no_stc_no_optitype+['Gender']].groupby(['Gender']).agg([np.mean, np.std])

In [ ]:
 errors_metadata_hla_I_df[labels_no_stc+['Gender']].groupby(['Gender']).mean().unstack().plot(kind='bar')

In [ ]:
 errors_metadata_hla_II_df[labels_no_stc_no_optitype+['Gender']].groupby(['Gender']).mean().unstack().plot(kind='bar')

# Analysis of overlap of samples 
Is there an overlap between the samples used in this study and the samples used in the development of the individual tools.

In [ ]:
sample_library_filepath = 'C:\\Users\\nikol\\OneDrive\\DTU\\11_semester\\Data\\'

samples_used_in_tools_dict = dict()

for tool in ['kourami', 'hla-la', 'optitype', 'hisatgenotype']:
    full_filepath = sample_library_filepath + tool + "_samples.txt"
    
    tmp_list = list()
    
    #Read all lines with samples used in study
    with open(full_filepath, 'r') as infile:
        for line in infile:
            
            tmp_list.append(line[:-1])
    
    
    #Only include those, which are also included in the 819 samples in this study:
    filtered_tmp_list = list(set(list(MG_exome_df.index)) & set(tmp_list))
    
    samples_used_in_tools_dict[tool] = len(list(filtered_tmp_list))
        

In [ ]:
already_used_samples_df = pd.DataFrame(samples_used_in_tools_dict, index=['n_samples'])
already_used_samples_df

In [ ]:
plt.bar(range(len(already_used_samples_df.columns)), list(already_used_samples_df.values[0]), align='center', alpha=0.5, color = '#0000FF')

plt.xticks(range(len(already_used_samples_df.columns)), ['kourami', 'hla-la', 'optitype', 'hisatgenotype'], rotation = 45)
plt.ylim(0,100)
plt.ylabel('N samples')
plt.title('Overview of samples used both in this study\n and in the development of the individual tools')
plt.show()

# Analysis of HISAT-genotype's alternative reads


In [ ]:
hisatgenotype_result_filepath = resultpath + '\\hisatgenotype\\'

hisatgenotype_files = []
for (dirpath, dirnames, filenames) in walk(hisatgenotype_result_filepath):
    hisatgenotype_files.extend(filenames)
    
#print(hisatgenotype_files)

#Save two predictions. One, with one guess per allele and one with the full prediction
hisatgenotype_results = dict()

hisatgenotype_results_ambiguous = dict()


for filename in hisatgenotype_files:
    if filename.endswith('.txt'):
    
        hisatgenotype_resultlist = list()
        
        hisatgenotype_resultlist_ambiguous = list()
        
        
        with open(hisatgenotype_result_filepath + filename) as infile:
            for line in infile:
                result = re.match(r'^\t+(1|2)\sranked (A|B|C|DRB1|DQB1)',line)
                
                ambiguous_result = re.match(r'^\t+\d\sranked (A|B|C|DRB1|DQB1)',line)

                if result is not None:
                    hisatgenotype_resultlist.append(line.split()[2])
                
                if ambiguous_result is not None:
                    hisatgenotype_resultlist_ambiguous.append(line.split()[2])

                    
            #Duplicate prediction for an allele in case of homologous case, so that each gene has two predictions.
            #In a homologous case, both result dicts only have one prediction and both needs an update.
            for allele in ['A', 'B', 'C', 'DRB1', 'DQB1']:
                allele_list = [pred for pred in hisatgenotype_resultlist if pred.startswith(allele)]

                if len(allele_list) == 1:
                    hisatgenotype_resultlist.append(allele_list[0])
                    hisatgenotype_resultlist.sort()
                    
                    hisatgenotype_resultlist_ambiguous.append(allele_list[0])
                    hisatgenotype_resultlist_ambiguous.sort()
                    
                    
                    

        hisatgenotype_results[filename[:-4]] = [i.split('*')[0] + '*' + i.split('*')[1].split(':')[0] + ':' + i.split('*')[1].split(':')[1] for i in hisatgenotype_resultlist]
        
        hisatgenotype_results_ambiguous[filename[:-4]] = [i.split('*')[0] + '*' + i.split('*')[1].split(':')[0] + ':' + i.split('*')[1].split(':')[1] for i in hisatgenotype_resultlist_ambiguous]
        
        
#hisatgenotype_results           
        

In [ ]:
#Find out a percentage of how much the true allele is an alternative suggestion, when HISAT-genotype mistypes: 

# Old code

### The distribution of the depth:

In [ ]:
# matplotlib histogram
plt.hist(error_dataframe_hla_I['mean_depth'], color = 'blue', edgecolor = 'black',
         bins = int(180/5))

# seaborn histogram
sns.distplot(error_dataframe_hla_I['mean_depth'], hist=True, kde=False, 
             bins=int(180/5), color = 'blue',
             hist_kws={'edgecolor':'black'})
# Add labels
plt.title('Histogram of mean sequencing depth for region')
plt.xlabel('mean sequencing depth')
plt.ylabel('Number of alleles')

In [ ]:
#Can one do this - maybe, idk. Check distributions. pvalue is however not below 0.05, so no significant difference
male_mean_errors = errors_metadata_hla_I_df[errors_metadata_hla_I_df['Gender'] == 'male']['mean_error_graph']
female_mean_errors = errors_metadata_hla_I_df[errors_metadata_hla_I_df['Gender'] == 'female']['mean_error_graph']

from scipy import stats
print(stats.ttest_ind(male_mean_errors, female_mean_errors))


In [ ]:
#Check for distribution of errors in males and females:
# matplotlib histogram
plt.hist(male_mean_errors, color = 'blue', edgecolor = 'black',
         bins = int(180/5), range=[0, 6])

# seaborn histogram
sns.distplot(male_mean_errors, hist=True, kde=False, 
             bins=int(180/5), color = 'blue',
             hist_kws={'edgecolor':'black'})
# Add labels
plt.title('Histogram of mean sequencing depth for region')
plt.xlabel('mean sequencing depth')
plt.ylabel('Number of alleles')

In [ ]:
#Check for distribution of errors in males and females:
# matplotlib histogram
plt.hist(female_mean_errors, color = 'blue', edgecolor = 'black',
         bins = int(180/5), range=[0, 6])


# # seaborn histogram
# sns.distplot(female_mean_errors, hist=True, kde=False, 
#              bins=int(180/5), color = 'blue',
#              hist_kws={'edgecolor':'black'})
# Add labels
plt.title('Histogram of mean sequencing depth for region')
plt.xlabel('mean sequencing depth')
plt.ylabel('Number of alleles')

In [ ]:

#Can one do this - maybe, idk. Check distributions. pvalue is however not below 0.05, so no significant difference
male_mean_errors = errors_metadata_hla_II_df[errors_metadata_hla_II_df['Gender'] == 'male']['mean_error_graph']
female_mean_errors = errors_metadata_hla_II_df[errors_metadata_hla_II_df['Gender'] == 'female']['mean_error_graph']

from scipy import stats
print(stats.ttest_ind(male_mean_errors, female_mean_errors))

In [ ]:
#Check for distribution of errors in males and females:
# matplotlib histogram
plt.hist(male_mean_errors, color = 'blue', edgecolor = 'black',
         bins = int(180/5), range=[0, 6])

# seaborn histogram
sns.distplot(male_mean_errors, hist=True, kde=False, 
             bins=int(180/5), color = 'blue',
             hist_kws={'edgecolor':'black'})
# Add labels
plt.title('Histogram of mean sequencing depth for region')
plt.xlabel('mean sequencing depth')
plt.ylabel('Number of alleles')

In [ ]:
#Check for distribution of errors in males and females:
# matplotlib histogram
plt.hist(female_mean_errors, color = 'blue', edgecolor = 'black',
         bins = int(180/5), range=[0, 6])


# # seaborn histogram
# sns.distplot(female_mean_errors, hist=True, kde=False, 
#              bins=int(180/5), color = 'blue',
#              hist_kws={'edgecolor':'black'})
# Add labels
plt.title('Histogram of mean sequencing depth for region')
plt.xlabel('mean sequencing depth')
plt.ylabel('Number of alleles')

In [ ]:
errors_metadata_df[labels_no_stc+['Region','Population']].groupby(['Region','Population']).mean().unstack().plot(kind='bar', figsize= (20,10))

In [ ]:
errors_metadata_df[labels_no_stc+['Region','Population']].groupby(['Region','Population']).mean().unstack().plot(kind='bar', figsize= (20,10))